### Итоговый проект. Оценка районов города Санкт-Петербург по безопасности дорожного движения

Требуется разработать метрику, которая позволит оценить безопасность районов

Исходный набор данных ДТП в городах взят с сайта проекта [Карта ДТП](https://dtp-stat.ru/opendata)


Импортируем требуемые библиотеки

In [1]:
import pandas as pd
import geopandas as gpd
import numpy as np
import osmnx as ox
import requests
import osm2geojson
from keplergl import KeplerGl

Прочитаем файл с авариями

In [2]:
data = gpd.read_file("sankt-peterburg.geojson").to_crs(4326)

Загрузим данные для Адмиралтейского района и визуализируем данные.

In [7]:
district_Adm = data[data['region'] == 'Адмиралтейский район']
district_Adm

id                                     light  \
44564  2647682                       Светлое время суток   
44565  2647691  В темное время суток, освещение включено   
44566  2647692                       Светлое время суток   
44567  2647725  В темное время суток, освещение включено   
44568  2647732  В темное время суток, освещение включено   
...        ...                                       ...   
46529  1931064                       Светлое время суток   
46530  1931188                       Светлое время суток   
46531  1931242  В темное время суток, освещение включено   
46532  1901456                       Светлое время суток   
46533  1932478  В темное время суток, освещение включено   

                                       point                region scheme  \
44564  {'lat': 59.927899, 'long': 30.319498}  Адмиралтейский район    800   
44565  {'lat': 59.902842, 'long': 30.314562}  Адмиралтейский район    820   
44566  {'lat': 59.924157, 'long': 30.323403}  Адмиралтейский район    740   
44567  {'lat': 59.922103, 'long': 30.336621}  Адмиралтейский район    740   
44568  {'lat': 59.902708, 'long': 30.276282}  Адмиралтейский район    830   
...                                      ...                   ...    ...   
46529  {'lat': 59.910556, 'long': 30.306667}  Адмиралтейский район    300   
46530  {'lat': 59.919167, 'long': 30.277778}  Адмиралтейский район    880   
46531  {'lat': 59.903889, 'long': 30.318056}  Адмиралтейский район    950   
46532  {'lat': 59.922923, 'long': 30.322398}  Адмиралтейский район    720   
46533  {'lat': 59.909444, 'long': 30.275556}  Адмиралтейский район    700   

                                               address  \
44564              г Санкт-Петербург, пер Спасский, 14   
44565              г Санкт-Петербург, ул Красуцкого, 3   
44566         г Санкт-Петербург, наб Реки Фонтанки, 93   
44567          г Санкт-Петербург, ул Звенигородская, 3   
44568  г Санкт-Петербург, пр-кт Старо-Петергофский, 44   
...                                                ...   
46529       г Санкт-Петербург, пр-кт Измайловский, 23А   
46530              г Санкт-Петербург, ул Витебская, 20   
46531          г Санкт-Петербург, пр-кт Московский, 73   
46532        г Санкт-Петербург, ул Введенский канал, 2   
46533  г Санкт-Петербург, пр-кт Старо-Петергофский, 14   

                     category            datetime     severity  dead_count  \
44564       Наезд на пешехода 2021-11-21 14:10:00       Легкий           0   
44565       Наезд на пешехода 2021-11-19 08:30:00      Тяжёлый           0   
44566       Наезд на пешехода 2021-11-24 09:45:00       Легкий           0   
44567       Наезд на пешехода 2021-11-18 18:20:00       Легкий           0   
44568  Наезд на велосипедиста 2021-11-18 19:05:00       Легкий           0   
...                       ...                 ...          ...         ...   
46529            Столкновение 2015-10-27 09:44:00  С погибшими           1   
46530       Наезд на пешехода 2015-10-11 16:00:00      Тяжёлый           0   
46531    Наезд на препятствие 2015-10-04 18:30:00      Тяжёлый           0   
46532       Наезд на пешехода 2018-01-09 18:00:00       Легкий           0   
46533       Наезд на пешехода 2015-02-13 00:15:00  С погибшими           1   

       injured_count    parent_region  participants_count  \
44564              1  Санкт-Петербург                   2   
44565              1  Санкт-Петербург                   2   
44566              1  Санкт-Петербург                   2   
44567              1  Санкт-Петербург                   2   
44568              1  Санкт-Петербург                   2   
...              ...              ...                 ...   
46529              2  Санкт-Петербург                   7   
46530              1  Санкт-Петербург                   2   
46531              1  Санкт-Петербург                   2   
46532              1  Санкт-Петербург                   2   
46533              0  Санкт-Петербург                   2   


In [8]:
district_Adm['geometry'].explore(tiles="CartoDB positron")

Как видно, в данных присутсвуют ошибки месторасположения аварий, а поэтому для расчета метрики будем ориентироваться на указание названия района. 

Загрузим данные для остальных районов.

In [3]:
district_Adm_met = data[data['region'] == 'Адмиралтейский район']
district_Vas_met = data[data['region'] == 'Василеостровский район']
district_Vb_met = data[data['region'] == 'Выборгский район']
district_Ka_met = data[data['region'] == 'Калининский район']
district_Kir_met = data[data['region'] == 'Кировский район']
district_Kol_met = data[data['region'] == 'Колпинский район']
district_Kras_met = data[data['region'] == 'Красногвардейский район']
district_Krasn_met = data[data['region'] == 'Красносельский район']
district_Kronsh_met = data[data['region'] == 'Кронштадтский район']
district_Kur_met = data[data['region'] == 'Курортный район']
district_Mos_met = data[data['region'] == 'Московский район']
district_Nev_met = data[data['region'] == 'Невский район']
district_Petr_met = data[data['region'] == 'Петроградский район']
district_Prim_met = data[data['region'] == 'Приморский район']
district_Petrodv_met = data[data['region'] == 'Петродворцовый район']
district_Push_met = data[data['region'] == 'Пушкинский район']
district_Frunz_met = data[data['region'] == 'Фрунзенский район']
district_Cent_met = data[data['region'] == 'Центральный район']

Создадим итоговый список районов Санкт-Петербурга

In [4]:
districts_name = ['Адмиралтейский р-он',
                'Василиостровский р-он',
                'Выборгский р-он',
                'Калиниский р-он',
                'Кировский р-он',
                'Колпинский р-он',
                'Красногвардейский р-он',
                'Красносельский р-он',
                'Кронштадский р-он',
                'Курортный р-он',
                'Московский р-он',
                'Невский р-он',
                'Петроградский р-он',
                'Петродворцовый р-он',
                'Приморский р-он',
                'Пушкинский р-он',
                'Фрунзенский р-он',
                'Центральный р-он']

Найдем количество дорожных происшествий в каждом районе

In [5]:
count_accidents = [district_Adm_met.shape[0],
                   district_Vas_met.shape[0],
                   district_Vb_met.shape[0],
                   district_Ka_met.shape[0],
                   district_Kir_met.shape[0],
                   district_Kol_met.shape[0],
                   district_Kras_met.shape[0],
                   district_Krasn_met.shape[0],
                   district_Kronsh_met.shape[0],
                   district_Kur_met.shape[0],
                   district_Mos_met.shape[0],
                   district_Nev_met.shape[0],
                   district_Petr_met.shape[0],
                   district_Prim_met.shape[0],
                   district_Petrodv_met.shape[0],
                   district_Push_met.shape[0],
                   district_Frunz_met.shape[0],
                   district_Cent_met.shape[0]]

### Расчет метрики
Метрика для каждого района рассчитывается следующим образом: $100 * \dfrac{acc_{dist}}{acc_{all}}$

где: 

* $acc_{dist}$ - ДТП в конкретном районе
* $acc_{all}$ - ДТП во всем городе
* $100$ - коэффициент, который позволяет получить "бальную" систему оценки

In [6]:
final_list = []
list_metrics = []
for count in count_accidents:
    list_metrics.append((int)(100*(count/sum(count_accidents))))
final_list = dict(zip(districts_name,list_metrics))
final_list  

{'Адмиралтейский р-он': 4,
 'Василиостровский р-он': 3,
 'Выборгский р-он': 9,
 'Калиниский р-он': 8,
 'Кировский р-он': 6,
 'Колпинский р-он': 3,
 'Красногвардейский р-он': 6,
 'Красносельский р-он': 6,
 'Кронштадский р-он': 0,
 'Курортный р-он': 2,
 'Московский р-он': 8,
 'Невский р-он': 8,
 'Петроградский р-он': 3,
 'Петродворцовый р-он': 8,
 'Приморский р-он': 2,
 'Пушкинский р-он': 4,
 'Фрунзенский р-он': 6,
 'Центральный р-он': 6}

Как видно, наибольшее количество ДТП происходит в Выборгском районе. Визуализируем данный район по маске, а также загрузим данные для других районов.

Для анализа каждого района получим ссылки на OSM объекты 

In [8]:
TERRITORY_NAME_Adm = "R1114193" #Адмиралтейский
TERRITORY_NAME_Vas = "R1114252" #Василиостровский
TERRITORY_NAME_Vb = "R1114354" #Выборгский
TERRITORY_NAME_Ka = "R1114806" #Калиниский
TERRITORY_NAME_Kir = "R1114809" #Кировский
TERRITORY_NAME_Kol = "R337424" #Колпинский
TERRITORY_NAME_Kras = "R1114895" #Красногвардейский
TERRITORY_NAME_Krasn = "R363103" #Красносельский
TERRITORY_NAME_Kronsh = "R1115082" #Кронштадский
TERRITORY_NAME_Kur = "R1115366" #Курортный
TERRITORY_NAME_Mos = "R338636" #Московский
TERRITORY_NAME_Nev = "R368287" #Невский
TERRITORY_NAME_Petr = "R1114905" #Петроградский
TERRITORY_NAME_Petrodv = "R367375" #Петродворцовый
TERRITORY_NAME_Prim = "R1115367" #Приморский
TERRITORY_NAME_Push = "R338635" #Пушкинский
TERRITORY_NAME_Frunz = "R369514" #Фрунзенский
TERRITORY_NAME_Cent= "R1114902" #Центральный

Загрузка geogataframe с территориями районов

In [9]:
district_Adm = ox.geocode_to_gdf([TERRITORY_NAME_Adm], by_osmid=True)
district_Vas = ox.geocode_to_gdf([TERRITORY_NAME_Vas], by_osmid=True)
district_Vb = ox.geocode_to_gdf([TERRITORY_NAME_Vb], by_osmid=True)
district_Ka = ox.geocode_to_gdf([TERRITORY_NAME_Ka], by_osmid=True)
district_Kir = ox.geocode_to_gdf([TERRITORY_NAME_Kir], by_osmid=True)
district_Kol = ox.geocode_to_gdf([TERRITORY_NAME_Kol], by_osmid=True)
district_Kras = ox.geocode_to_gdf([TERRITORY_NAME_Kras], by_osmid=True)
district_Krasn = ox.geocode_to_gdf([TERRITORY_NAME_Krasn], by_osmid=True)
district_Kronsh = ox.geocode_to_gdf([TERRITORY_NAME_Kronsh], by_osmid=True)
district_Kur = ox.geocode_to_gdf([TERRITORY_NAME_Kur], by_osmid=True)
district_Mos = ox.geocode_to_gdf([TERRITORY_NAME_Mos], by_osmid=True)
district_Nev = ox.geocode_to_gdf([TERRITORY_NAME_Nev], by_osmid=True)
district_Petr = ox.geocode_to_gdf([TERRITORY_NAME_Petr], by_osmid=True)
district_Prim = ox.geocode_to_gdf([TERRITORY_NAME_Prim], by_osmid=True)
district_Petrodv = ox.geocode_to_gdf([TERRITORY_NAME_Petrodv], by_osmid=True)
district_Push = ox.geocode_to_gdf([TERRITORY_NAME_Push], by_osmid=True)
district_Frunz = ox.geocode_to_gdf([TERRITORY_NAME_Frunz], by_osmid=True)
district_Cent = ox.geocode_to_gdf([TERRITORY_NAME_Cent], by_osmid=True)

Проведем по маскам районов загрузку ДТП

In [10]:
gdf_Adm = gpd.read_file("sankt-peterburg.geojson", mask=district_Adm).to_crs(4326)
gdf_Vas = gpd.read_file("sankt-peterburg.geojson", mask=district_Vas).to_crs(4326)
gdf_Vb = gpd.read_file("sankt-peterburg.geojson", mask=district_Vb).to_crs(4326)
gdf_Ka = gpd.read_file("sankt-peterburg.geojson", mask=district_Ka).to_crs(4326)
gdf_Kir = gpd.read_file("sankt-peterburg.geojson", mask=district_Kir).to_crs(4326)
gdf_Kol = gpd.read_file("sankt-peterburg.geojson", mask=district_Kol).to_crs(4326)
gdf_Kras = gpd.read_file("sankt-peterburg.geojson", mask=district_Kras).to_crs(4326)
gdf_Krasn = gpd.read_file("sankt-peterburg.geojson", mask=district_Krasn).to_crs(4326)
gdf_Kronsh = gpd.read_file("sankt-peterburg.geojson", mask=district_Kronsh).to_crs(4326)
gdf_Kur = gpd.read_file("sankt-peterburg.geojson", mask=district_Kur).to_crs(4326)
gdf_Mos = gpd.read_file("sankt-peterburg.geojson", mask=district_Mos).to_crs(4326)
gdf_Nev = gpd.read_file("sankt-peterburg.geojson", mask=district_Nev).to_crs(4326)
gdf_Petr = gpd.read_file("sankt-peterburg.geojson", mask=district_Petr).to_crs(4326)
gdf_Prim = gpd.read_file("sankt-peterburg.geojson", mask=district_Prim).to_crs(4326)
gdf_Petrodv = gpd.read_file("sankt-peterburg.geojson", mask=district_Petrodv).to_crs(4326)
gdf_Push = gpd.read_file("sankt-peterburg.geojson", mask=district_Push).to_crs(4326)
gdf_Frunz = gpd.read_file("sankt-peterburg.geojson", mask=district_Frunz).to_crs(4326)
gdf_Cent = gpd.read_file("sankt-peterburg.geojson", mask=district_Cent).to_crs(4326)

Во избежании проблем с отображением данных преобразуем дату происшествия в строку

In [11]:
gdf_Adm['datetime'] = gdf_Adm['datetime'].astype(str)
gdf_Vas['datetime'] = gdf_Vas['datetime'].astype(str)
gdf_Vb['datetime'] = gdf_Vb['datetime'].astype(str)
gdf_Ka['datetime'] = gdf_Ka['datetime'].astype(str)
gdf_Kir['datetime'] = gdf_Kir['datetime'].astype(str)
gdf_Kol['datetime'] = gdf_Kol['datetime'].astype(str)
gdf_Kras['datetime'] = gdf_Kras['datetime'].astype(str)
gdf_Krasn['datetime'] = gdf_Krasn['datetime'].astype(str)
gdf_Kronsh['datetime'] = gdf_Kronsh['datetime'].astype(str)
gdf_Kur['datetime'] = gdf_Kur['datetime'].astype(str)
gdf_Mos['datetime'] = gdf_Mos['datetime'].astype(str)
gdf_Nev['datetime'] = gdf_Nev['datetime'].astype(str)
gdf_Petr['datetime'] = gdf_Petr['datetime'].astype(str)
gdf_Prim['datetime'] = gdf_Prim['datetime'].astype(str)
gdf_Petrodv['datetime'] = gdf_Petrodv['datetime'].astype(str)
gdf_Push['datetime'] = gdf_Push['datetime'].astype(str)
gdf_Frunz['datetime'] = gdf_Frunz['datetime'].astype(str)
gdf_Cent['datetime'] = gdf_Cent['datetime'].astype(str)

Проверим корректность работы. 

In [12]:
gdf_Kronsh.explore(tiles="CartoDB positron")

Для каждого района проведем фильтрацию данных. Уберем из данных для каждого района случайно попавшие туда данные, для которых район происшествия не совпадает с маской района.

In [23]:
gdf_Adm_fix = gdf_Adm[gdf_Adm['region'] == 'Адмиралтейский район']
gdf_Vas_fix = gdf_Vas[gdf_Vas['region'] == 'Василеостровский район']
gdf_Vb_fix = gdf_Vb[gdf_Vb['region'] == 'Выборгский район']
gdf_Ka_fix = gdf_Ka[gdf_Ka['region'] == 'Калининский район']
gdf_Kir_fix = gdf_Kir[gdf_Kir['region'] == 'Кировский район']
gdf_Kol_fix = gdf_Kol[gdf_Kol['region'] == 'Колпинский район']
gdf_Kras_fix = gdf_Kras[gdf_Kras['region'] == 'Красногвардейский район']
gdf_Krasn_fix = gdf_Krasn[gdf_Krasn['region'] == 'Красносельский район']
gdf_Kronsh_fix = gdf_Kronsh[gdf_Kronsh['region'] == 'Кронштадтский район']
gdf_Kur_fix = gdf_Kur[gdf_Kur['region'] == 'Курортный район']
gdf_Mos_fix = gdf_Mos[gdf_Mos['region'] == 'Московский район']
gdf_Nev_fix = gdf_Nev[gdf_Nev['region'] == 'Невский район']
gdf_Petr_fix = gdf_Petr[gdf_Petr['region'] == 'Петроградский район']
gdf_Prim_fix = gdf_Prim[gdf_Prim['region'] == 'Приморский район']
gdf_Petrodv_fix = gdf_Petrodv[gdf_Petrodv['region'] == 'Петродворцовый район']
gdf_Push_fix = gdf_Push[gdf_Push['region'] == 'Пушкинский район']
gdf_Frunz_fix = gdf_Frunz[gdf_Frunz['region'] == 'Фрунзенский район']
gdf_Cent_fix = gdf_Cent[gdf_Cent['region'] == 'Центральный район']

Визуализируем дороги, которые находятся в Выборгском районе.

In [34]:
gdf_streets = gpd.read_file('streets.geojson', mask = district_Vb)
gdf_streets.explore(tiles="CartoDB positron")

Выполним запрос к overpass для получения данных о светофорах в городе Санкт-Петербург, а затем выделим только те, что находятся в Выборгском районе.

In [35]:
def get_city_bounds(city, city_crs):
    
    overpass_url = "http://overpass-api.de/api/interpreter"
    overpass_query = f"""
    [out:json];
            area['name'='{city}']->.searchArea;
            (
              node["highway"="traffic_signals"](area.searchArea);
            );
    out geom;
    """
    result = requests.get(overpass_url, params={'data': overpass_query}).json()
    bounds = osm2geojson.json2geojson(result)
    bounds = gpd.GeoDataFrame.from_features(bounds["features"]).set_crs(4326).to_crs(city_crs)
    

    return bounds

In [36]:
trafic_lights = get_city_bounds('Санкт-Петербург', 32636)

In [15]:
trafic_lights.explore(tiles="CartoDB positron")

Для визуализации в Kepler создадим geojson файл.

In [25]:
trafic_lights.to_file('traficlights.geojson', driver='GeoJSON')

Выделим светофоры по маске требуемого района.

In [37]:
trafic_lights_gdf = gpd.read_file('traficlights.geojson', mask = district_Vb)
trafic_lights_gdf.explore(tiles="CartoDB positron")

Отдельно добавим колонки долготы и широты места происшествия для визуализации

In [38]:
gdf_Vb["lon"] = gdf_Vb.to_crs(3857).geometry.centroid.to_crs(4326).x
gdf_Vb["lat"] = gdf_Vb.to_crs(3857).geometry.centroid.to_crs(4326).y
gdf_Vb

id                                     light  \
0     1927492                       Светлое время суток   
1     1927608                       Светлое время суток   
2     1918827                       Светлое время суток   
3     1909447                       Светлое время суток   
4     1929656                       Светлое время суток   
...       ...                                       ...   
4173  1914685                       Светлое время суток   
4174  1930205  В темное время суток, освещение включено   
4175  1908643                       Светлое время суток   
4176  1908792                       Светлое время суток   
4177  1921741  В темное время суток, освещение включено   

                                      point                  region scheme  \
0         {'lat': 59.9839, 'long': 30.3367}       Центральный район    710   
1         {'lat': 59.9839, 'long': 30.3369}       Центральный район    710   
2         {'lat': 59.9842, 'long': 30.3481}       Центральный район    740   
3     {'lat': 59.978056, 'long': 30.323056}        Московский район    720   
4         {'lat': 59.9711, 'long': 30.3339}        Московский район    090   
...                                     ...                     ...    ...   
4173   {'lat': 60.07743, 'long': 30.184937}        Выборгский район    910   
4174      {'lat': 60.0033, 'long': 30.3289}        Выборгский район    850   
4175  {'lat': 59.999292, 'long': 30.347275}        Выборгский район    850   
4176   {'lat': 60.052685, 'long': 30.32675}        Выборгский район    740   
4177  {'lat': 60.083056, 'long': 30.244167}  Василеостровский район    740   

                                                address              category  \
0                  г Санкт-Петербург, пр-кт Невский, 56     Наезд на пешехода   
1                  г Санкт-Петербург, пр-кт Невский, 56     Наезд на пешехода   
2                 г Санкт-Петербург, пр-кт Литейный, 59     Наезд на пешехода   
3                г Санкт-Петербург, пр-кт Дунайский, 24     Наезд на пешехода   
4     г Санкт-Петербург, ул Воздухоплавательная, Пар...  Наезд на препятствие   
...                                                 ...                   ...   
4173  г Санкт-Петербург, А-118 Кольцевая автомобильн...   Наезд на стоящее ТС   
4174  г Санкт-Петербург, пл Светлановская, 23 по пр....     Наезд на пешехода   
4175          г Санкт-Петербург, пр-кт Институтский, 11     Наезд на пешехода   
4176           г Санкт-Петербург, ул Хошимина, 13 кор.1     Наезд на пешехода   
4177                  г Санкт-Петербург, ул Детская, 15     Наезд на пешехода   

                 datetime severity  dead_count  injured_count  \
0     2016-05-09 18:00:00   Легкий           0              1   
1     2016-05-03 17:55:00   Легкий           0              2   
2     2017-01-21 13:30:00   Легкий           0              1   
3     2015-07-11 12:40:00  Тяжёлый           0              1   
4     2016-08-29 14:30:00   Легкий           0              1   
...                   ...      ...         ...            ...   
4173  2020-07-20 11:40:00  Тяжёлый           0              1   
4174  2016-11-15 15:20:00   Легкий           0              1   
4175  2018-02-19 09:02:00   Легкий           0              1   
4176  2018-02-08 09:20:00  Тяжёлый           0              1   
4177  2015-11-13 17:30:00   Легкий           0              1   

        parent_region  participants_count                   geometry  \
0     Санкт-Петербург                   2  POINT (30.33670 59.98390)   
1     Санкт-Петербург                   3  POINT (30.33690 59.98390)   
2     Санкт-Петербург                   2  POINT (30.34810 59.98420)   
3     Санкт-Петербург                   2  POINT (30.32306 59.97806)   
4     Санкт-Петербург                   1  POINT (30.33390 59.97110)   
...               ...                 ...                        ...   
4173  Санкт-Петербург                   2  POINT (30.18494 60.07743)   
4174  Санкт-Петербург              

Визуализация в Kepler

In [39]:
map = KeplerGl(height=1920, width=1080)
map.add_data(data=gdf_streets, name='Roads')
map.add_data(data=trafic_lights_gdf, name='Trafic Lights')
map.add_data(data=gdf_Vb, name='Accidents')
map

User Guide: https://docs.kepler.gl/docs/keplergl-jupyter


KeplerGl(data={'Roads': {'index': [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 2…